# Identifying Missing Data in the Caltrans/PeMS Dataset

The California Department of Transportation (Caltrans) collects data that describes the flow of traffic on California freeways. Caltrans stores these data in a database called PeMS. The data describe the number of counts per unit time meaured by roughly 45,000 sensors on a 30-second cadence. The type of sensor varies considerably, e.g. radar and magnetometers (see Chapter 1 of the [Introduction to PeMS User Guide](https://pems.dot.ca.gov/Papers/PeMS_Intro_User_Guide_v6.pdf)). 

In some cases, these data are missing. Faulty or broken sensors do not collect data. Or sensor data is not wirelessly transmitted back to PeMS. In addition, Caltrans performs some calculations to convert these raw sensor data into physical observables such as speed. These calculations include some assumptions such as the length of the vehicle, or $g$. Based on the quality of the assumption, these data can include errors.

In this notebook, we will take a look at the nature of the missing data. Some questions to ask:
1. Are all the data available for District 5 from the District Map and County Chart during 2023?
2. If data are missing, do they occur in any spatial or temporal clusters?
3. Are there any outliers or unexpected values in the data?
4. Are all the data available for all the available districts in recent decade, 2013-2023? And again, is there any pattern to the missing data? Are there any odd values?

### Setup

In [1]:
import ibis
import os
import itertools

import numpy as np
import pandas as pd
import seaborn as sns
import altair as alt
import ibis.selectors as s
import matplotlib.pyplot as plt
import matplotlib.dates as mdates

from dotenv import load_dotenv
from functools import reduce
from datetime import datetime as dt_obj
from datetime import date
from datetime import timedelta

%matplotlib inline
%config InlineBackend.figure_format = 'retina'

pd.set_option('display.max_columns', 200)
pd.set_option('display.max_rows', 3000)

In [2]:
load_dotenv(override=True)
USERNAME = os.getenv('USERNAME')
PASSWORD = os.getenv('PASSWORD')

In [3]:
con = ibis.snowflake.connect(
    user=USERNAME,
    password=PASSWORD,
    role='TRANSFORMER_DEV',
    warehouse='TRANSFORMING_XS_DEV',
    account="VSB79059-DSE_CALTRANS_PEMS",
    database="RAW_PRD/CLEARINGHOUSE",
)

In [4]:
station_metadata = con.table("STATION_META");
station_raw = con.table("STATION_RAW");
#station_status = con.table("STATION_STATUS");

/Users/monica.bobra/Library/Caches/pypoetry/virtualenvs/caldata-mdsa-caltrans-pems-4CtDAEQU-py3.10/lib/python3.10/site-packages/ibis/backends/snowflake/__init__.py:268: UserWarning: Unable to create map UDFs, some functionality will not work: 003001 (42501): SQL access control error:
Insufficient privileges to operate on account 'NGB13288'
  warnings.warn(


In [5]:
station_metadata_df = station_metadata.execute(limit=10)
station_raw_df = station_raw.execute(limit=10)
#station_status_df = station_status.execute(limit=10)

In [6]:
station_metadata_df

FILENAME      ID FWY DIR DISTRICT  \
0  clhouse/meta/d08/2024/01/d08_text_meta_2024_01...  801230  10   W        8   
1  clhouse/meta/d08/2024/01/d08_text_meta_2024_01...  801231  10   W        8   
2  clhouse/meta/d08/2024/01/d08_text_meta_2024_01...  801232  10   E        8   
3  clhouse/meta/d08/2024/01/d08_text_meta_2024_01...  801233  10   E        8   
4  clhouse/meta/d08/2024/01/d08_text_meta_2024_01...  801234  10   W        8   
5  clhouse/meta/d08/2024/01/d08_text_meta_2024_01...  801236  10   W        8   
6  clhouse/meta/d08/2024/01/d08_text_meta_2024_01...  801237  10   E        8   
7  clhouse/meta/d08/2024/01/d08_text_meta_2024_01...  801238  10   E        8   
8  clhouse/meta/d08/2024/01/d08_text_meta_2024_01...  801239  10   E        8   
9  clhouse/meta/d08/2024/01/d08_text_meta_2024_01...  801240  10   W        8   

  COUNTY   CITY STATE_PM  ABS_PM   LATITUDE   LONGITUDE  LENGTH TYPE  LANES  \
0     71  48788     .591  47.356  34.082004 -117.699964   0.845   ML      4   
1     71  48788     .591  47.356  34.082004 -117.699964     NaN   OR      2   
2     71  48788     .721  47.486  34.082149 -117.697705   0.996   ML      4   
3     71  48788     .721  47.486  34.082149 -117.697705     NaN   OR      2   
4     71  48788    1.168  47.933  34.085065 -117.690768   0.660   ML      4   
5     71  48788    1.168  47.933  34.085065 -117.690768     NaN   OR      2   
6     71  48788    1.342  48.107  34.086058 -117.687970   0.595   ML      4   
7     71  48788    1.342  48.107  34.086058 -117.687970     NaN   OR      2   
8     71  81344    1.912  48.677  34.087192 -117.678250   0.523   ML      4   
9     71  81344    1.912  48.677  34.087372 -117.678335   0.544   ML      4   

              NAME USER_ID_1 USER_ID_2 USER_ID_3 USER_ID_4  
0  MONTE VISTA AVE         1      None      None      None  
1  MONTE VISTA AVE         1      None      None      None  
2  MONTE VISTA AVE         1      None      None      None  
3  MONTE VISTA AVE         1      None      None      None  
4      CENTRAL AVE         1      None      None      None  
5      CENTRAL AVE         1      None      None      None  
6      CENTRAL AVE         1      None      None      None  
7      CENTRAL AVE         1      None      None      None  
8       BENSON AVE         1      None      None      None  
9       BENSON AVE         1      None      None      None

In [7]:
station_raw_df

FILENAME    SAMPLE_TIMESTAMP  \
0  clhouse/raw/d07/2021/04/d07_text_station_raw_2... 2021-04-23 03:17:38   
1  clhouse/raw/d08/2021/04/d08_text_station_raw_2... 2021-04-23 03:02:43   
2  clhouse/raw/d12/2021/04/d12_text_station_raw_2... 2021-04-23 01:19:33   
3  clhouse/raw/d10/2021/04/d10_text_station_raw_2... 2021-04-23 23:21:30   
4  clhouse/raw/d04/2021/04/d04_text_station_raw_2... 2021-04-23 23:36:43   
5  clhouse/raw/d07/2021/04/d07_text_station_raw_2... 2021-04-23 01:34:00   
6  clhouse/raw/d12/2021/04/d12_text_station_raw_2... 2021-04-23 22:35:04   
7  clhouse/raw/d08/2021/04/d08_text_station_raw_2... 2021-04-23 05:24:36   
8  clhouse/raw/d05/2021/04/d05_text_station_raw_2... 2021-04-23 10:48:51   
9  clhouse/raw/d04/2021/04/d04_text_station_raw_2... 2021-04-23 00:15:53   

  SAMPLE_DATE         ID  FLOW_1  OCCUPANCY_1  SPEED_1  FLOW_2  OCCUPANCY_2  \
0  2021-04-23     767597       0        0.000      NaN     0.0       0.0000   
1  2021-04-23     814496       0        0.000      0.0     0.0       0.0000   
2  2021-04-23    1204357       1        0.006    101.0     2.0       0.0140   
3  2021-04-23    1081310       1        0.014     31.0     NaN          NaN   
4  2021-04-23     406720       0        0.000      NaN     1.0       0.0111   
5  2021-04-23     718394       0        0.000      NaN     1.0       0.0067   
6  2021-04-23    1221571       0        0.000      0.0     0.0       0.0000   
7  2021-04-23     825694       6        0.033    101.0     NaN          NaN   
8  2021-04-23  500010072      13        0.109     66.0     8.0       0.0680   
9  2021-04-23     413784       0        0.000      NaN     NaN          NaN   

   SPEED_2  FLOW_3  OCCUPANCY_3  SPEED_3  FLOW_4  OCCUPANCY_4  SPEED_4  \
0      NaN     0.0        0.000      NaN     0.0        0.000      NaN   
1      0.0     NaN          NaN      NaN     NaN          NaN      NaN   
2     77.0     1.0        0.032     17.0     2.0        0.051     22.0   
3      NaN     NaN          NaN      NaN     NaN          NaN      NaN   
4      NaN     NaN          NaN      NaN     NaN          NaN      NaN   
5      NaN     0.0        0.000      NaN     0.0        0.000      NaN   
6      0.0     NaN          NaN      NaN     NaN          NaN      NaN   
7      NaN     NaN          NaN      NaN     NaN          NaN      NaN   
8     66.0     NaN          NaN      NaN     NaN          NaN      NaN   
9      NaN     NaN          NaN      NaN     NaN          NaN      NaN   

   FLOW_5  OCCUPANCY_5  SPEED_5  FLOW_6  OCCUPANCY_6  SPEED_6  FLOW_7  \
0     0.0          0.0      NaN     NaN          NaN      NaN     NaN   
1     NaN          NaN      NaN     NaN          NaN      NaN     NaN   
2     0.0          0.0      0.0     NaN          NaN      NaN     NaN   
3     NaN          NaN      NaN     NaN          NaN      NaN     NaN   
4     NaN          NaN      NaN     NaN          NaN      NaN     NaN   
5     NaN          NaN      NaN     NaN          NaN      NaN     NaN   
6     NaN          NaN      NaN     NaN          NaN      NaN     NaN   
7     NaN          NaN      NaN     NaN          NaN      NaN     NaN   
8     NaN          NaN      NaN     NaN          NaN      NaN     NaN   
9     NaN          NaN      NaN     NaN          NaN      NaN     NaN   

   OCCUPANCY_7  SPEED_7  FLOW_8  OCCUPANCY_8  SPEED_8  
0          NaN      NaN     NaN          NaN      NaN  
1          NaN      NaN     NaN          NaN      NaN  
2          NaN      NaN     NaN          NaN      NaN  
3          NaN      NaN     NaN          NaN      NaN  
4          NaN      NaN     NaN          NaN      NaN  
5          NaN      NaN     NaN          NaN      NaN  
6          NaN      NaN     NaN          NaN      NaN  
7          NaN      NaN     NaN          NaN      NaN  
8          NaN      NaN     NaN          NaN      NaN  
9          NaN      NaN     NaN          NaN      NaN

### Question 1. Are all the data available for District 5 from the [District Map and County Chart](https://cwwp2.dot.ca.gov/documentation/district-map-county-chart.htm) during 2023?

1. Filter the station metadata file to look at `DISTRICT` values of 5.
2. Strip away all old versions of the data by selecting the most recent unique ID.
3. Select all station IDs within District 5 that took data in 2023.
4. Merge the raw and metadata files on the keyword `ID`.
5. Create a coverage map of the timestamps for all freeways using the keyword `SAMPLE_TIMESTAMP`.

##### 1. Filter the station metadata file to look at `DISTRICT` values of 5.

In [8]:
district_5_filter = station_metadata.filter(station_metadata["DISTRICT"] == "5")

In [9]:
district_5_df = district_5_filter.execute()

##### 2. Strip away all old versions of the data by selecting the most recent unique ID.

Identify the number of unique values of ID in District 5.

In [10]:
print('There are {} unique values of ID in District 5.'.format(district_5_df['ID'].nunique()))

There are 706 unique values of ID in District 5.


Construct a new column called `DATA_VERSION`.

In [11]:
district_5_df['DATA_VERSION'] = np.NaN

Extract the date from the `FILENAME` keyword. Populate these dates in the `DATA_VERSION` keyword.

In [12]:
data_version = [dt_obj.strptime(filename[39:49], '%Y_%m_%d') for filename in district_5_df['FILENAME'].values]

In [13]:
district_5_df['DATA_VERSION'] = data_version

Select the most recent `DATA_VERSION` for each unique ID. Drop the rest. The dataframe `district_5_recent_version_df` contains the most recent metadata values for each station ID.

In [14]:
unique_IDs = district_5_df['ID'].value_counts().index.to_list()

In [15]:
drop_these_rows = []
for i in range(len(unique_IDs)):
    ID_subset = district_5_df[district_5_df['ID'] == unique_IDs[i]]
    index_for_max_value = ID_subset['DATA_VERSION'].idxmax()
    indices_for_rows_to_drop = ID_subset.drop(index_for_max_value).index.to_list()
    drop_these_rows.append(indices_for_rows_to_drop)

In [16]:
drop_these_rows_flattened = list(itertools.chain.from_iterable(drop_these_rows))

In [17]:
district_5_recent_version_df = district_5_df.drop(drop_these_rows_flattened).reset_index(drop=True)

Have some of these data been updated in 2023? Yes.

In [18]:
max(district_5_recent_version_df['DATA_VERSION'])

Timestamp('2023-11-17 00:00:00')

##### 3. Select all station IDs within District 5 that took data in 2023.

Selecting dates using a datetime object will call the Snowflake [date_from_parts()](https://docs.snowflake.com/en/sql-reference/functions/date_from_parts) function, which will search through all the partitions. To optimize the query, select dates in string format. Selecting one year of data for one district takes 3.5 minutes of execution time, but 9.5 minutes of wall time. See [this query](https://app.snowflake.com/vsb79059/dse_caltrans_pems/#/compute/history/queries/01b18b20-0001-fb1d-003e-3887000f305e). However, there is not enough memory to merge the metadata and raw dataframes on the keyword `ID`.

In [19]:
# Select dates within the year 2023
date_selection_start = '2023-03-01'
date_selection_end = '2023-03-30'

In [20]:
print(date_selection_start)
print(date_selection_end)

2023-03-01
2023-03-30


In [21]:
date_and_ID_filter = station_raw.select("SAMPLE_DATE","SAMPLE_TIMESTAMP","FILENAME","ID").filter(
    (station_raw["SAMPLE_DATE"] >= date_selection_start) & (station_raw["SAMPLE_DATE"] < date_selection_end)
).filter(
    station_raw["FILENAME"].contains("/d05")
).select("ID","SAMPLE_TIMESTAMP")

In [22]:
%%time
out = date_and_ID_filter.execute()

CPU times: user 11.4 s, sys: 2.58 s, total: 13.9 s
Wall time: 46.3 s


In [23]:
# A list of all the station IDs that took data in 2023
IDs_in_D5_with_2023_data = out['ID'].value_counts().index.to_list();
len(IDs_in_D5_with_2023_data)

570

##### 4. Merge the raw and metadata files on the keyword `ID`.

In [24]:
merged_df = out.merge(district_5_recent_version_df, on=['ID'], how='left')

In [38]:
unique_station_ids = merged_df["ID"].value_counts().index.to_list()

##### 5. Create a coverage map of the timestamps for all freeways using the keyword `SAMPLE_TIMESTAMP`.

In [42]:
sample = len(unique_station_ids)
print(sample)

570


In [43]:
%%time

# Setup
fig, ax = plt.subplots(figsize=(24, 100), layout="constrained")
ax.set(title="Traffic Sensor Coverage Map \n District 5 \n March 1, 2023 to March 30, 2023")
odi_mustard = "#E3881B"
odi_purple = "#7560C1"

# Plot the coverage map
y_labels = []
for i in range(sample):
    print(i)
    # Extract the timestamps for one station
    sample_timestamp = merged_df[merged_df["ID"] == unique_station_ids[i]].sort_values(["SAMPLE_TIMESTAMP"]).reset_index(drop=True).SAMPLE_TIMESTAMP.values
    # Create the y_values
    y_values = np.full_like(np.arange(len(sample_timestamp)), i)
    # Plot the coverage for this station
    ax.plot(sample_timestamp, y_values, "-|", color=odi_mustard, markerfacecolor=odi_mustard, markersize=10, alpha=0.4)
    #ax.plot(sample_timestamp, y_values, "|", color=white, markerfacecolor=white, markersize=10, alpha=1.0)
    # Generate the label for this station
    freeway = str(merged_df[merged_df["ID"] == unique_station_ids[i]]["FWY"].iloc[0])
    direction = str(merged_df[merged_df["ID"] == unique_station_ids[i]]["DIR"].iloc[0])
    y_label = freeway + ' ' + direction + ', ID ' + str(unique_station_ids[i])
    y_labels.append(y_label)

# Plot labels
plt.setp(ax.get_xticklabels(), rotation=30, ha="right")
ax.yaxis.set_ticks(list(range(sample)), y_labels)
ax.spines[["left", "top", "right"]].set_visible(False)

# Display
plt.show()

## Save
#fig.savefig('district5_coverage.png', dpi=300, transparent=False, bbox_inches='tight')

0
1
2
3
4
5
6
7
8
9
10
11
12
13
14
15
16
17
18
19
20
21
22
23
24
25
26
27
28
29
30
31
32
33
34
35
36
37
38
39
40
41
42
43
44
45
46
47
48
49
50
51
52
53
54
55
56
57
58
59
60
61
62
63
64
65
66
67
68
69
70
71
72
73
74
75
76
77
78
79
80
81
82
83
84
85
86
87
88
89
90
91
92
93
94
95
96
97
98
99
100
101
102
103
104
105
106
107
108
109
110
111
112
113
114
115
116
117
118
119
120
121
122
123
124
125
126
127
128
129
130
131
132
133
134
135
136
137
138
139
140
141
142
143
144
145
146
147
148
149
150
151
152
153
154
155
156
157
158
159
160
161
162
163
164
165
166
167
168
169
170
171
172
173
174
175
176
177
178
179
180
181
182
183
184
185
186
187
188
189
190
191
192
193
194
195
196
197
198
199
200
201
202
203
204
205
206
207
208
209
210
211
212
213
214
215
216
217
218
219
220
221
222
223
224
225
226
227
228
229
230
231
232
233
234
235
236
237
238
239
240
241
242
243
244
245
246
247
248
249
250
251
252
253
254
255
256
257
258
259
260
261
262
263
264
265
266
267
268
269
270
271
272
273
274
275
276
27

CPU times: user 36min 22s, sys: 10.5 s, total: 36min 32s
Wall time: 36min 41s


In [44]:
fig.savefig('district5_coverage.png', dpi=300, transparent=False, bbox_inches='tight')